In [0]:
spark

SparkSession - hive 
 
 
 SparkContext 

 Spark UI 

 
 Version 
 v3.3.2 
 Master 
 local[8] 
 AppName 
 Databricks Shell

In [0]:
from pyspark.sql.types import StructField, StructField, IntegerType, StringType, BooleanType, DateType, DecimalType
from pyspark.sql.functions import asc

In [0]:
from pyspark.sql import SparkSession
spark = SparkSession.builder.appName("IPL-analysis").getOrCreate()

In [0]:
from pyspark.sql.functions import col, when, sum, avg, row_number
from pyspark.sql.functions import sum, col, max
from pyspark.sql.functions import col, format_number
from pyspark.sql.functions import col, sum, count, avg, expr, when, round, lower

In [0]:
from pyspark.sql.types import StructType

In [0]:
from pyspark.sql import functions as F

Add each dataset (object) one by one. Only adding is not enough, you we will also have to change/ match the datatype according to the original datastructure.

In [0]:
# Create a new schema for this dataset ball_by_ball_schema (object):

ball_by_ball_schema = StructType([
    StructField("match_id", IntegerType(), True),
    StructField("over_id", IntegerType(), True),
    StructField("ball_id", IntegerType(), True),
    StructField("innings_no", IntegerType(), True),
    StructField("team_batting", StringType(), True),
    StructField("team_bowling", StringType(), True),
    StructField("striker_batting_position", IntegerType(), True),
    StructField("extra_type", StringType(), True),
    StructField("runs_scored", IntegerType(), True),
    StructField("extra_runs", IntegerType(), True),
    StructField("wides", IntegerType(), True),
    StructField("legbyes", IntegerType(), True),
    StructField("byes", IntegerType(), True),
    StructField("noballs", IntegerType(), True),
    StructField("penalty", IntegerType(), True),
    StructField("bowler_extras", IntegerType(), True),
    StructField("out_type", StringType(), True),
    StructField("caught", BooleanType(), True),
    StructField("bowled", BooleanType(), True),
    StructField("run_out", BooleanType(), True),
    StructField("lbw", BooleanType(), True),
    StructField("retired_hurt", BooleanType(), True),
    StructField("stumped", BooleanType(), True),
    StructField("caught_and_bowled", BooleanType(), True),
    StructField("hit_wicket", BooleanType(), True),
    StructField("obstructingfeild", BooleanType(), True),
    StructField("bowler_wicket", BooleanType(), True),
    StructField("match_date", DateType(), True),
    StructField("season", IntegerType(), True),
    StructField("striker", IntegerType(), True),
    StructField("non_striker", IntegerType(), True),
    StructField("bowler", IntegerType(), True),
    StructField("player_out", IntegerType(), True),
    StructField("fielders", IntegerType(), True),
    StructField("striker_match_sk", IntegerType(), True),
    StructField("strikersk", IntegerType(), True),
    StructField("nonstriker_match_sk", IntegerType(), True),
    StructField("nonstriker_sk", IntegerType(), True),
    StructField("fielder_match_sk", IntegerType(), True),
    StructField("fielder_sk", IntegerType(), True),
    StructField("bowler_match_sk", IntegerType(), True),
    StructField("bowler_sk", IntegerType(), True),
    StructField("playerout_match_sk", IntegerType(), True),
    StructField("battingteam_sk", IntegerType(), True),
    StructField("bowlingteam_sk", IntegerType(), True),
    StructField("keeper_catch", BooleanType(), True),
    StructField("player_out_sk", IntegerType(), True),
    StructField("matchdatesk", DateType(), True)
])

In [0]:
# Now we will load each datafile from S3 bucket one by one
# ball_by_ball

ball_by_ball_df = spark.read.schema(ball_by_ball_schema).format("csv").option("header", "true").load("s3://ipl-data-analysis-project/Ball_By_Ball.csv")

One dataset is done, we have to do this for all other datasets (objects) from the AWS S3 bucket.

In [0]:
match_schema = StructType([
    StructField("match_sk", IntegerType(), True),
    StructField("match_id", IntegerType(), True),
    StructField("team1", StringType(), True),
    StructField("team2", StringType(), True),
    StructField("match_date", DateType(), True),
    StructField("season_year", IntegerType(), True),  # YearType is not available in PySpark, use IntegerType instead
    StructField("venue_name", StringType(), True),
    StructField("city_name", StringType(), True),
    StructField("country_name", StringType(), True),
    StructField("toss_winner", StringType(), True),
    StructField("match_winner", StringType(), True),
    StructField("toss_name", StringType(), True),
    StructField("win_type", StringType(), True),
    StructField("outcome_type", StringType(), True),
    StructField("manofmach", StringType(), True),
    StructField("win_margin", IntegerType(), True),
    StructField("country_id", IntegerType(), True)
])

In [0]:
# match Schema

match_df = spark.read.schema(match_schema).format("csv").option("header", "true").load("s3://ipl-data-analysis-project/Match.csv")

In [0]:
# Player Schema

player_schema = StructType([
    StructField("player_sk", IntegerType(), True),
    StructField("player_id", IntegerType(), True),
    StructField("player_name", StringType(), True),
    StructField("dob", DateType(), True),
    StructField("batting_hand", StringType(), True),
    StructField("bowling_skill", StringType(), True),
    StructField("country_name", StringType(), True)
])

In [0]:
player_df = spark.read.schema(player_schema).format("csv").option("header", "true").load("s3://ipl-data-analysis-project/Player.csv")

In [0]:
# player_match schema

player_match_schema = StructType([
    StructField("player_match_sk", IntegerType(), True),
    StructField("playermatch_key", DecimalType(), True),  # Using DecimalType for precision handling
    StructField("match_id", IntegerType(), True),
    StructField("player_id", IntegerType(), True),
    StructField("player_name", StringType(), True),
    StructField("dob", DateType(), True),
    StructField("batting_hand", StringType(), True),
    StructField("bowling_skill", StringType(), True),
    StructField("country_name", StringType(), True),
    StructField("role_desc", StringType(), True),
    StructField("player_team", StringType(), True),
    StructField("opposit_team", StringType(), True),
    StructField("season_year", IntegerType(), True),  # YearType is not available in PySpark, use IntegerType instead
    StructField("is_manofthematch", BooleanType(), True),
    StructField("age_as_on_match", IntegerType(), True),
    StructField("isplayers_team_won", BooleanType(), True),
    StructField("batting_status", StringType(), True),
    StructField("bowling_status", StringType(), True),
    StructField("player_captain", StringType(), True),
    StructField("opposit_captain", StringType(), True),
    StructField("player_keeper", StringType(), True),
    StructField("opposit_keeper", StringType(), True)
])

In [0]:
player_match_df = spark.read \
    .schema(player_match_schema) \
    .format("csv") \
    .option("header", "true") \
    .load("s3://ipl-data-analysis-project/Player_match.csv")

In [0]:
# Team schema

team_schema = StructType([
    StructField("team_sk", IntegerType(), True),
    StructField("team_id", IntegerType(), True),
    StructField("team_name", StringType(), True)
])

In [0]:
team_df = spark.read \
    .schema(team_schema) \
    .format("csv") \
    .option("header", "true") \
    .load("s3://ipl-data-analysis-project/Team.csv")

In [0]:
player_match_df.show(5)

+---------------+---------------+--------+---------+-----------+----+--------------+--------------------+------------+---------+--------------------+--------------------+-----------+----------------+---------------+------------------+--------------+--------------+--------------+---------------+-------------+--------------+
|player_match_sk|playermatch_key|match_id|player_id|player_name| dob|  batting_hand|       bowling_skill|country_name|role_desc|         player_team|        opposit_team|season_year|is_manofthematch|age_as_on_match|isplayers_team_won|batting_status|bowling_status|player_captain|opposit_captain|player_keeper|opposit_keeper|
+---------------+---------------+--------+---------+-----------+----+--------------+--------------------+------------+---------+--------------------+--------------------+-----------+----------------+---------------+------------------+--------------+--------------+--------------+---------------+-------------+--------------+
|             -1|        

In [0]:
from pyspark.sql import functions as F

# Join ball_by_ball with match to get the season information
ball_match_df = ball_by_ball_df.join(match_df, ball_by_ball_df.match_id == match_df.match_id)

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.functions import col, sum, count, avg

In [0]:
# Joining DataFrames on match_id
ball_match_df = ball_by_ball_df.join(match_df, on="match_id", how="inner")

## 1. Basic Filtering for wide and no balls

In [0]:
# Filter to include only valid deliveries (excluding extras like wides and no balls for specific analyses)
ball_by_ball_df = ball_by_ball_df.filter((col("wides") == 0) & (col("noballs")==0))

In [0]:
# Aggregation: Calculate the total and average runs scored in each match and inning
total_and_avg_runs = ball_by_ball_df.groupBy("match_id", "innings_no").agg(
    sum(col("runs_scored")).alias("total_runs"),
    (sum(col("runs_scored")) / count(col("runs_scored"))).alias("average_runs per ball")  # average_runs = total_runs / number of balls
)

In [0]:
total_and_avg_runs.show(5)

+--------+----------+----------+---------------------+
|match_id|innings_no|total_runs|average_runs per ball|
+--------+----------+----------+---------------------+
|  980940|         1|       138|                 1.15|
|  419132|         1|       162|                 1.35|
| 1082632|         2|       202|   1.9238095238095239|
|  335993|         2|       131|   1.6794871794871795|
| 1082617|         1|       123|   1.0512820512820513|
+--------+----------+----------+---------------------+
only showing top 5 rows



## 2. Peak Performance Analysis:
 Question: Which players achieve the highest peak scores in a single inning over multiple seasons?
 
 Task: Group data by player and season, then identify the maximum score in a single inning for each player across seasons. Analyze the consistency of reaching these peak scores.


In [0]:
runs_by_innings = ball_by_ball_df.groupBy("match_id", "striker", "season").agg(
    sum(col("runs_scored")).alias("runs_in_innings")
)

In [0]:
runs_by_innings = runs_by_innings.withColumn("runs_in_innings", col("runs_in_innings").cast("int"))

In [0]:
peak_scores = runs_by_innings.groupBy("striker").agg(
    max(col("runs_in_innings")).alias("max_runs")
).orderBy(col("max_runs").desc())

peak_scores.show(5)

+-------+--------+
|striker|max_runs|
+-------+--------+
|    162|     171|
|      2|     158|
|    110|     132|
|    185|     127|
|    187|     126|
+-------+--------+
only showing top 5 rows



In [0]:
# This is an optional step, we can join peak scores with names

peak_scores_with_names = peak_scores.join(player_df, peak_scores.striker == player_df.player_id) \
  .select("striker","Player_Name", "max_runs")\
    .orderBy(col("max_runs").desc())

In [0]:
peak_scores_with_names.show(10)

+-------+--------------+--------+
|striker|   Player_Name|max_runs|
+-------+--------------+--------+
|    162|      CH Gayle|     171|
|      2|   BB McCullum|     158|
|    110|AB de Villiers|     132|
|    185|       M Vijay|     127|
|    187|     DA Warner|     126|
|     41|      V Sehwag|     122|
|    167|   PC Valthaty|     120|
|     56|     A Symonds|     117|
|     19|    MEK Hussey|     116|
|     62|       WP Saha|     115|
+-------+--------------+--------+
only showing top 10 rows



# 3.Economy Rate of Bowlers in Different Phases of the Game:

Question: What are the economy rates of bowlers during the powerplay, middle overs, and death overs?

Task: Segment the ball-by-ball data into different match phases, calculate the total runs conceded and total balls bowled by each bowler during these phases, and then compute the economy rate.

In [0]:
ball_by_ball_over = ball_by_ball_df.withColumn(
  "phase",
  when(col("over_id").between(1,6), "Power Play")
  .when(col("over_id").between(7,15), "Middle Overs")
  .when(col("over_id").between(16,20), "Death Overs")
  .otherwise("Other")
)

In [0]:
distinct_overs = ball_by_ball_df.select("over_id").distinct().orderBy(asc("over_id"))
distinct_overs.show(20)

+-------+
|over_id|
+-------+
|      1|
|      2|
|      3|
|      4|
|      5|
|      6|
|      7|
|      8|
|      9|
|     10|
|     11|
|     12|
|     13|
|     14|
|     15|
|     16|
|     17|
|     18|
|     19|
|     20|
+-------+



In [0]:
ball_by_ball_over.select("phase", "over_id").distinct().show(10)

+------------+-------+
|       phase|over_id|
+------------+-------+
|Middle Overs|     11|
|  Power Play|      2|
|Middle Overs|     10|
|Middle Overs|     15|
|Middle Overs|     13|
|  Power Play|      1|
| Death Overs|     17|
|  Power Play|      3|
|Middle Overs|     12|
| Death Overs|     16|
+------------+-------+
only showing top 10 rows



In [0]:
runs_balls_per_phase = ball_by_ball_over.groupBy("bowler", "phase").agg(
    sum(col("runs_scored")).alias("total_runs_conceded"),
    count(col("ball_id")).alias("total_balls_bowled")
)

In [0]:
runs_balls_per_phase = runs_balls_per_phase.withColumn(
    "economy_rate",
    col("total_runs_conceded") / (col("total_balls_bowled") / 6)
)

# adding bolwer names instead of bowler id
joing_bolwer_names = runs_balls_per_phase.join(player_df, runs_balls_per_phase.bowler == player_df.player_id)

joing_bolwer_names = joing_bolwer_names.withColumnRenamed("player_name", "bowler_name")

#runs_balls_per_phase.show(10)
joing_bolwer_names.show(5)

+------+------------+-------------------+------------------+-----------------+---------+---------+---------------+----+--------------+--------------------+------------+
|bowler|       phase|total_runs_conceded|total_balls_bowled|     economy_rate|player_sk|player_id|    bowler_name| dob|  batting_hand|       bowling_skill|country_name|
+------+------------+-------------------+------------------+-----------------+---------+---------+---------------+----+--------------+--------------------+------------+
|   305|Middle Overs|                373|               270| 8.28888888888889|      304|      305|     GJ Maxwell|null|Right-hand bat|  Right-arm offbreak|   Australia|
|   378| Death Overs|                247|               202|7.336633663366337|      377|      378|       MA Starc|null| Left-hand bat|       Left-arm fast|   Australia|
|   363|Middle Overs|                 64|                48|              8.0|      362|      363|  KW Richardson|null|Right-hand bat|Right-arm fast-me...|

In [0]:
joing_bolwer_names = joing_bolwer_names.select("bowler_name", "phase", "total_runs_conceded", "total_balls_bowled", "economy_rate")
joing_bolwer_names.show(5)

+---------------+------------+-------------------+------------------+-----------------+
|    bowler_name|       phase|total_runs_conceded|total_balls_bowled|     economy_rate|
+---------------+------------+-------------------+------------------+-----------------+
|     GJ Maxwell|Middle Overs|                373|               270| 8.28888888888889|
|       MA Starc| Death Overs|                247|               202|7.336633663366337|
|  KW Richardson|Middle Overs|                 64|                48|              8.0|
|      JJ Bumrah| Death Overs|                650|               420|9.285714285714286|
|C de Grandhomme|Middle Overs|                105|                82|7.682926829268293|
+---------------+------------+-------------------+------------------+-----------------+
only showing top 5 rows



#4. Impact of Fielding on Match Outcomes:

Question: How does the number of catches and run-outs by a team correlate with winning matches?

Task: Aggregate the number of catches and run-outs per team per match, correlate these with match outcomes to see if higher fielding stats lead to a higher probability of winning.


In [0]:
fielding_stats = ball_by_ball_df.groupBy("match_id", "team_bowling").agg(
    sum(when(col("out_type") == "caught", 1).otherwise(0)).alias("catches"),
    sum(when(col("out_type") == "run out", 1).otherwise(0)).alias("run_outs")
)

In [0]:
# Join fielding stats with match results
match_results = match_df.select("match_id", "match_winner")

# Combine fielding stats with match outcomes
fielding_with_results = fielding_stats.join(match_results, "match_id")

In [0]:
correlation_stats = fielding_with_results.groupBy("team_bowling").agg(
    sum("catches").alias("total_catches"),
    sum("run_outs").alias("total_run_outs"),
    count("match_id").alias("total_matches")
)

In [0]:
correlation_stats = correlation_stats.join(team_df, correlation_stats.team_bowling == team_df.team_id)

In [0]:
correlation_stats.select(
    "team_name", "total_catches", "total_run_outs", "total_matches"
).show()

+--------------------+-------------+--------------+-------------+
|           team_name|total_catches|total_run_outs|total_matches|
+--------------------+-------------+--------------+-------------+
|      Mumbai Indians|          409|            80|          140|
| Sunrisers Hyderabad|          187|            34|           62|
| Chennai Super Kings|          433|            78|          131|
|     Deccan Chargers|          224|            38|           75|
|    Rajasthan Royals|          345|            79|          118|
|    Delhi Daredevils|          368|           100|          132|
|Kochi Tuskers Kerala|           27|            12|           14|
|Kolkata Knight Ri...|          335|            90|          132|
|       Pune Warriors|          129|            18|           46|
|     Kings XI Punjab|          359|            67|          134|
|Rising Pune Super...|           37|             6|           14|
|       Gujarat Lions|           41|             6|           16|
|Royal Cha

# 5.Toss Advantage Analysis:

Question: Does winning the toss give teams a significant advantage in terms of winning matches?

Task: Compare the match outcomes with the toss results to find any statistical significance in match-winning probabilities for the toss-winning team.

In [0]:
# Select relevant columns from match_df
toss_and_outcome = match_df.select("match_id", "toss_winner", "match_winner")

In [0]:
toss_and_outcome = toss_and_outcome.withColumn(
    "toss_winner_won_match",
    when(toss_and_outcome.toss_winner == toss_and_outcome.match_winner, 1).otherwise(0)
)

In [0]:
toss_stats = toss_and_outcome.agg(
    count("match_id").alias("total_matches"),
    sum("toss_winner_won_match").alias("toss_winner_wins")
)


In [0]:
toss_stats = toss_stats.withColumn(
    "win_percentage",
    format_number((col("toss_winner_wins") / col("total_matches")) * 100, 2)
)

In [0]:
toss_stats.show()

+-------------+----------------+--------------+
|total_matches|toss_winner_wins|win_percentage|
+-------------+----------------+--------------+
|          637|             324|         50.86|
+-------------+----------------+--------------+



##### Based on the analysis, teams that win the toss go on to win the match about 50.86% of the time. This suggests that there is a potential advantage to winning the toss.

# 6.Performance Under Pressure:

Question: Which batsmen perform best under pressure, defined as batting in the last five overs or when chasing a steep target?

Task: Identify innings where batsmen batted in the last five overs or while chasing a target over 6 runs per over, and calculate their average and strike rate.

In [0]:
last_five_overs = ball_by_ball_df.filter(col("over_id").between(16, 20))

In [0]:
match_df = match_df.withColumn("required_run_rate", col("win_margin") / 20).filter(col("required_run_rate") > 6)

In [0]:
steep_target_innings = ball_by_ball_df.join(match_df, "match_id").filter(col("team_batting") != col("match_winner"))

In [0]:
last_five_overs = last_five_overs.select("match_id", "over_id", "ball_id", "striker", "runs_scored", "team_batting", "out_type")
steep_target_innings = steep_target_innings.select("match_id", "over_id", "ball_id", "striker", "runs_scored", "team_batting", "out_type")

In [0]:
pressure_scenarios = last_five_overs.union(steep_target_innings)

In [0]:
performance_under_pressure = pressure_scenarios.groupBy("striker").agg(
    sum(col("runs_scored")).alias("total_runs"),
    count("ball_id").alias("balls_faced"),
    sum(when(col("out_type").isNotNull(), 1).otherwise(0)).alias("dismissals")
)

In [0]:
performance_under_pressure = performance_under_pressure.withColumn(
    "average",
    format_number(col("total_runs") / col("dismissals"), 2)
).withColumn(
    "strike_rate",
    format_number((col("total_runs") * 100) / col("balls_faced"), 2)
)

In [0]:
performance_with_names = performance_under_pressure.join(player_df, performance_under_pressure.striker == player_df.player_id).select(
    "player_name", "average", "strike_rate"
)

In [0]:
performance_with_names.orderBy(col("average").desc(), col("strike_rate").desc()).show(10)

+-------------+-------+-----------+
|  player_name|average|strike_rate|
+-------------+-------+-----------+
|     DT Patil|   4.00|     400.00|
|     PA Reddy|   3.00|     300.00|
|  Salman Butt|   2.67|     266.67|
|CR Brathwaite|   2.42|     241.94|
|      HM Amla|   2.35|     235.29|
|  YV Takawale|   2.33|     233.33|
|    LPC Silva|   2.30|     230.00|
|    BJ Rohrer|   2.26|     225.71|
|   MA Agarwal|   2.25|     225.00|
|    LJ Wright|   2.23|     223.08|
+-------------+-------+-----------+
only showing top 10 rows



###### This output shows that certain batsmen perform exceptionally well under pressure, defined as batting in the last five overs or while chasing a steep target. The analysis highlights their batting averages and strike rates in these scenarios, providing insights into which players thrive in high-pressure situations.

In [0]:
player_match_df.select("bowling_skill").distinct().show(1000)

+--------------------+
|       bowling_skill|
+--------------------+
|    Right-arm medium|
|                null|
|    Right-arm bowler|
|Slow left-arm ort...|
|      Right-arm fast|
|�Right-arm medium...|
|Right-arm medium-...|
| �Right-arm offbreak|
|Right-arm medium ...|
|     Legbreak googly|
|Right-arm fast-me...|
|     Left-arm medium|
|      �Left-arm fast|
|Slow left-arm chi...|
|                 N/A|
|       Left-arm fast|
|Left-arm fast-medium|
|           �Legbreak|
|  Right-arm offbreak|
|Left-arm medium-fast|
|�Right-arm fast-m...|
|            Legbreak|
|                NULL|
+--------------------+



## 7. Home Ground Advantage:

Question: How significant is the home ground advantage in cricket?

Task: Compare team performance metrics (wins, runs scored, wickets taken) in home and away matches to evaluate the impact of playing at home.

In [0]:
match_df = match_df.withColumn(
    "location",
    when(col("team1") == col("match_winner"), "home").otherwise("away")
)

In [0]:
# Wins
team_wins = match_df.groupBy("match_winner", "location").agg(count("match_id").alias("wins"))

In [0]:
# Runs Scored
team_runs = ball_by_ball_df.join(match_df.select(col("match_id"), col("location").alias("match_location")), ball_by_ball_df.match_id == match_df.match_id).groupBy("team_batting", "match_location").agg(
    sum("runs_scored").alias("total_runs")
)

In [0]:
# Wickets Taken
team_wickets = ball_by_ball_df.join(match_df.select(col("match_id"), col("location").alias("match_location")), ball_by_ball_df.match_id == match_df.match_id).groupBy("team_bowling", "match_location").agg(
    sum(when(col("out_type").isNotNull(), 1).otherwise(0)).alias("total_wickets")
)

In [0]:
# Step 3: Analyze Differences
# Combine the metrics into a single DataFrame for comparison
performance_metrics = team_wins.join(
    team_runs, (team_wins.match_winner == team_runs.team_batting) & (team_wins.location == team_runs.match_location), "fullouter"
).join(
    team_wickets, (team_wins.match_winner == team_wickets.team_bowling) & (team_wins.location == team_wickets.match_location), "fullouter"
).select(
    col("match_winner").alias("team"),
    col("location"),
    col("wins"),
    col("total_runs"),
    col("total_wickets")
).orderBy("team", "location")

In [0]:
performance_metrics_new = performance_metrics.na.drop(subset=["team", "location", "wins"]).show(3)

+--------------------+--------+----+----------+-------------+
|                team|location|wins|total_runs|total_wickets|
+--------------------+--------+----+----------+-------------+
|Kolkata Knight Ri...|    away|   1|      null|         null|
|      Mumbai Indians|    away|   1|       193|           82|
|Royal Challengers...|    home|   3|      null|         null|
+--------------------+--------+----+----------+-------------+



# Now lets use PySpark SQL

In [0]:
from pyspark.sql import SparkSession
spark = SparkSession.builder.appName("Cricket Data Analysis").getOrCreate()


In [0]:
# Load the data
ball_by_ball_df = spark.read.csv("s3://ipl-data-analysis-project/Ball_By_Ball.csv", header=True, inferSchema=True)
player_df = spark.read.csv("s3://ipl-data-analysis-project/Player.csv", header=True, inferSchema=True)

# Register the DataFrame as a SQL temporary view
ball_by_ball_df.createOrReplaceTempView("ball_by_ball")
player_df.createOrReplaceTempView("Player")
match_df.createOrReplaceTempView("Match")
team_df.createOrReplaceTempView("Team")
player_match_df.createOrReplaceTempView("player_match")

# 1. find the maximum score by each player in any single innings

In [0]:
query1 = """
SELECT p.player_name, MAX(runs_in_innings) AS max_runs
FROM (
    SELECT match_id, innings_no, striker, SUM(runs_scored) AS runs_in_innings
    FROM ball_by_ball
    GROUP BY match_id, innings_no, striker
) r
JOIN Player p ON r.striker = p.player_id
GROUP BY p.player_name
ORDER BY max_runs DESC
"""

peak_scores = spark.sql(query1)
peak_scores.show(10)

+--------------+--------+
|   player_name|max_runs|
+--------------+--------+
|      CH Gayle|     175|
|   BB McCullum|     158|
|AB de Villiers|     133|
|       M Vijay|     127|
|     DA Warner|     126|
|      V Sehwag|     122|
|   PC Valthaty|     120|
|     A Symonds|     117|
|    MEK Hussey|     116|
|      SE Marsh|     115|
+--------------+--------+
only showing top 10 rows



# 2.Impact of Match Conditions on Team Performance:

Question: How do different playing conditions (home vs. away, day vs. night matches) affect team performance in terms of win rate?
Task: Analyze the win rates of teams under various match conditions. This can provide insights into how environmental or psychological factors influence game outcomes.

In [0]:
query2 = """
SELECT t.team_name, v.venue_name, COUNT(*) AS matches_won
FROM match m
JOIN Team t ON m.match_winner = t.team_name
JOIN (SELECT DISTINCT match_id, venue_name FROM match) v ON m.match_id = v.match_id
GROUP BY t.team_name, v.venue_name
ORDER BY matches_won DESC
"""

peak_scores = spark.sql(query2)
peak_scores.show()

+--------------------+--------------------+-----------+
|           team_name|          venue_name|matches_won|
+--------------------+--------------------+-----------+
|Royal Challengers...|M Chinnaswamy Sta...|          3|
|Kolkata Knight Ri...|M Chinnaswamy Sta...|          1|
|      Mumbai Indians|    Feroz Shah Kotla|          1|
+--------------------+--------------------+-----------+



# 3: Player Performance Trends Over Seasons
Goal: Analyze how players' performances (in terms of runs scored and wickets taken) trend over different seasons, helping to identify if a player is improving, consistent, or declining.

In [0]:
query3 = """
SELECT p.player_name, pm.season_year, SUM(b.runs_scored) AS total_runs, SUM(CASE WHEN b.bowler_wicket = TRUE THEN 1 ELSE 0 END) AS wickets
FROM ball_by_ball b
JOIN player_match pm ON b.match_id = pm.match_id AND b.striker = pm.player_id
JOIN player p ON pm.player_id = p.player_id
GROUP BY p.player_name, pm.season_year
ORDER BY p.player_name, pm.season_year
"""

peak_scores = spark.sql(query3)
peak_scores.show()


+--------------+-----------+----------+-------+
|   player_name|season_year|total_runs|wickets|
+--------------+-----------+----------+-------+
|A Ashish Reddy|       2012|        35|      4|
|A Ashish Reddy|       2013|       125|      6|
|A Ashish Reddy|       2015|        73|      2|
|A Ashish Reddy|       2016|        47|      1|
|    A Chandila|       2012|         0|      0|
|    A Chandila|       2013|         4|      0|
|      A Chopra|       2008|        42|      3|
|      A Chopra|       2009|        11|      1|
|   A Choudhary|       2017|        25|      1|
|    A Flintoff|       2009|        62|      2|
|      A Kumble|       2008|        13|      1|
|      A Kumble|       2009|        16|      1|
|      A Kumble|       2010|         6|      0|
|      A Mishra|       2008|        37|      3|
|      A Mishra|       2009|        26|      1|
|      A Mishra|       2010|        39|      4|
|      A Mishra|       2011|        68|      3|
|      A Mishra|       2012|        16| 

# 4: Analyzing Key Players' Impact on Match Outcomes
Goal: Determine which players most frequently influence the outcome of a match, either through scoring runs, taking wickets, or being declared Man of the Match.

In [0]:
query4 = """
SELECT p.player_name, COUNT(*) AS influential_games
FROM player_match pm
JOIN match m ON pm.match_id = m.match_id
JOIN player p ON pm.player_id = p.player_id
WHERE m.match_winner = pm.player_team OR pm.is_manofthematch = TRUE
GROUP BY p.player_name
ORDER BY influential_games DESC
"""

peak_scores = spark.sql(query4)
peak_scores.show()

+---------------+-----------------+
|    player_name|influential_games|
+---------------+-----------------+
| AB de Villiers|                3|
|       CH Gayle|                3|
|        V Kohli|                3|
|      S Aravind|                2|
|      YS Chahal|                2|
|       M Kartik|                2|
|     TM Dilshan|                1|
|     KA Pollard|                1|
|Mohammad Hafeez|                1|
|       HV Patel|                1|
|KB Arun Karthik|                1|
|      RG Sharma|                1|
|      STR Binny|                1|
|     RT Ponting|                1|
|     JD Unadkat|                1|
|     AB Agarkar|                1|
|         N Rana|                1|
|      HH Pandya|                1|
|      KV Sharma|                1|
|     SL Malinga|                1|
+---------------+-----------------+
only showing top 20 rows



In [0]:
pip install plotly pandas

Python interpreter will be restarted.
Python interpreter will be restarted.


In [0]:
import pandas as pd
import plotly as plt
import plotly.graph_objects as go
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns

In [0]:
# Execute SQL Query
team_toss_win_performance = spark.sql("""
    SELECT team1, COUNT(*) AS matches_played, SUM(CASE WHEN toss_winner = match_winner THEN 1 ELSE 0 END) AS wins_after_toss
    FROM match
    WHERE toss_winner = team1
    GROUP BY team1
    ORDER BY wins_after_toss DESC
""")

# Now since we have answered some important business/ sports analytics questions, lets create a new dataframe that is a combination of all the datasets we have - using Joins and CTEs.

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, BooleanType, DateType
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, DateType, BooleanType, DecimalType

In [0]:
spark = SparkSession.builder.appName("Cricket Data Analysis").getOrCreate()

ball_by_ball_schema = StructType([
    StructField("match_id", IntegerType(), True),
    StructField("over_id", IntegerType(), True),
    StructField("ball_id", IntegerType(), True),
    StructField("innings_no", IntegerType(), True),
    StructField("team_batting", StringType(), True),
    StructField("team_bowling", StringType(), True),
    StructField("striker_batting_position", IntegerType(), True),
    StructField("extra_type", StringType(), True),
    StructField("runs_scored", IntegerType(), True),
    StructField("extra_runs", IntegerType(), True),
    StructField("wides", IntegerType(), True),
    StructField("legbyes", IntegerType(), True),
    StructField("byes", IntegerType(), True),
    StructField("noballs", IntegerType(), True),
    StructField("penalty", IntegerType(), True),
    StructField("bowler_extras", IntegerType(), True),
    StructField("out_type", StringType(), True),
    StructField("caught", BooleanType(), True),
    StructField("bowled", BooleanType(), True),
    StructField("run_out", BooleanType(), True),
    StructField("lbw", BooleanType(), True),
    StructField("retired_hurt", BooleanType(), True),
    StructField("stumped", BooleanType(), True),
    StructField("caught_and_bowled", BooleanType(), True),
    StructField("hit_wicket", BooleanType(), True),
    StructField("obstructingfeild", BooleanType(), True),
    StructField("bowler_wicket", BooleanType(), True),
    StructField("match_date", DateType(), True),
    StructField("season", IntegerType(), True),
    StructField("striker", IntegerType(), True),
    StructField("non_striker", IntegerType(), True),
    StructField("bowler", IntegerType(), True),
    StructField("player_out", IntegerType(), True),
    StructField("fielders", IntegerType(), True),
    StructField("striker_match_sk", IntegerType(), True),
    StructField("strikersk", IntegerType(), True),
    StructField("nonstriker_match_sk", IntegerType(), True),
    StructField("nonstriker_sk", IntegerType(), True),
    StructField("fielder_match_sk", IntegerType(), True),
    StructField("fielder_sk", IntegerType(), True),
    StructField("bowler_match_sk", IntegerType(), True),
    StructField("bowler_sk", IntegerType(), True),
    StructField("playerout_match_sk", IntegerType(), True),
    StructField("battingteam_sk", IntegerType(), True),
    StructField("bowlingteam_sk", IntegerType(), True),
    StructField("keeper_catch", BooleanType(), True),
    StructField("player_out_sk", IntegerType(), True),
    StructField("matchdatesk", DateType(), True)
])

df_ball_by_ball = spark.read.schema(ball_by_ball_schema)\
    .format("csv")\
    .option("header", "true")\
    .load("s3://ipl-data-analysis-project/Ball_By_Ball.csv")

In [0]:
match_schema = StructType([
    StructField("match_sk", IntegerType(), True),
    StructField("match_id", IntegerType(), True),
    StructField("team1", StringType(), True),
    StructField("team2", StringType(), True),
    StructField("match_date", DateType(), True),
    StructField("season_year", IntegerType(), True),  # YearType is not available in PySpark, use IntegerType instead
    StructField("venue_name", StringType(), True),
    StructField("city_name", StringType(), True),
    StructField("country_name", StringType(), True),
    StructField("toss_winner", StringType(), True),
    StructField("match_winner", StringType(), True),
    StructField("toss_name", StringType(), True),
    StructField("win_type", StringType(), True),
    StructField("outcome_type", StringType(), True),
    StructField("manofmach", StringType(), True),
    StructField("win_margin", IntegerType(), True),
    StructField("country_id", IntegerType(), True)
])

df_match = spark.read.schema(match_schema) \
    .format("csv") \
    .option("header", "true") \
    .load("s3://ipl-data-analysis-project/Match.csv")

In [0]:
# Player Schema
player_schema = StructType([
    StructField("player_sk", IntegerType(), True),
    StructField("player_id", IntegerType(), True),
    StructField("player_name", StringType(), True),
    StructField("dob", DateType(), True),
    StructField("batting_hand", StringType(), True),
    StructField("bowling_skill", StringType(), True),
    StructField("country_name", StringType(), True)
])

df_player = spark.read.schema(player_schema) \
    .format("csv") \
    .option("header", "true") \
    .load("s3://ipl-data-analysis-project/Player.csv")

In [0]:
# player_match schema
player_match_schema = StructType([
    StructField("player_match_sk", IntegerType(), True),
    StructField("playermatch_key", DecimalType(), True),  # Using DecimalType for precision handling
    StructField("match_id", IntegerType(), True),
    StructField("player_id", IntegerType(), True),
    StructField("player_name", StringType(), True),
    StructField("dob", DateType(), True),
    StructField("batting_hand", StringType(), True),
    StructField("bowling_skill", StringType(), True),
    StructField("country_name", StringType(), True),
    StructField("role_desc", StringType(), True),
    StructField("player_team", StringType(), True),
    StructField("opposit_team", StringType(), True),
    StructField("season_year", IntegerType(), True),  # YearType is not available in PySpark, use IntegerType instead
    StructField("is_manofthematch", BooleanType(), True),
    StructField("age_as_on_match", IntegerType(), True),
    StructField("isplayers_team_won", BooleanType(), True),
    StructField("batting_status", StringType(), True),
    StructField("bowling_status", StringType(), True),
    StructField("player_captain", StringType(), True),
    StructField("opposit_captain", StringType(), True),
    StructField("player_keeper", StringType(), True),
    StructField("opposit_keeper", StringType(), True)
])

df_player_match = spark.read.schema(player_match_schema) \
    .format("csv") \
    .option("header", "true") \
    .load("s3://ipl-data-analysis-project/Player_match.csv")

In [0]:
# Team schema
team_schema = StructType([
    StructField("team_sk", IntegerType(), True),
    StructField("team_id", IntegerType(), True),
    StructField("team_name", StringType(), True)
])

df_team = spark.read.schema(team_schema) \
    .format("csv") \
    .option("header", "true") \
    .load("s3://ipl-data-analysis-project/Team.csv")

In [0]:
ball_by_ball_joined_match = df_ball_by_ball.join(df_match, "match_id", "inner")
ball_by_ball_joined_match.show()

+--------+-------+-------+----------+------------+------------+------------------------+----------+-----------+----------+-----+-------+----+-------+-------+-------------+--------------+------+------+-------+----+------------+-------+-----------------+----------+----------------+-------------+----------+------+-------+-----------+------+----------+--------+----------------+---------+-------------------+-------------+----------------+----------+---------------+---------+------------------+--------------+--------------+------------+-------------+-----------+--------+--------------------+----------------+----------+-----------+--------------------+---------+------------+--------------------+--------------------+---------+--------+------------+-------------+----------+----------+
|match_id|over_id|ball_id|innings_no|team_batting|team_bowling|striker_batting_position|extra_type|runs_scored|extra_runs|wides|legbyes|byes|noballs|penalty|bowler_extras|      out_type|caught|bowled|run_out| lbw|

In [0]:
player_match_joined_player = df_player_match.join(df_player, df_player_match["player_id"] == df_player["player_id"], "outer")
player_match_joined_player.show()

+---------------+---------------+--------+---------+-----------+----+-------------+----------------+------------+---------+--------------------+--------------------+-----------+----------------+---------------+------------------+--------------+--------------+--------------+---------------+-------------+--------------+---------+---------+-----------+----+-------------+----------------+------------+
|player_match_sk|playermatch_key|match_id|player_id|player_name| dob| batting_hand|   bowling_skill|country_name|role_desc|         player_team|        opposit_team|season_year|is_manofthematch|age_as_on_match|isplayers_team_won|batting_status|bowling_status|player_captain|opposit_captain|player_keeper|opposit_keeper|player_sk|player_id|player_name| dob| batting_hand|   bowling_skill|country_name|
+---------------+---------------+--------+---------+-----------+----+-------------+----------------+------------+---------+--------------------+--------------------+-----------+----------------+----

In [0]:
ball_by_ball_joined_match.printSchema()

root
 |-- match_id: integer (nullable = true)
 |-- over_id: integer (nullable = true)
 |-- ball_id: integer (nullable = true)
 |-- innings_no: integer (nullable = true)
 |-- team_batting: string (nullable = true)
 |-- team_bowling: string (nullable = true)
 |-- striker_batting_position: integer (nullable = true)
 |-- extra_type: string (nullable = true)
 |-- runs_scored: integer (nullable = true)
 |-- extra_runs: integer (nullable = true)
 |-- wides: integer (nullable = true)
 |-- legbyes: integer (nullable = true)
 |-- byes: integer (nullable = true)
 |-- noballs: integer (nullable = true)
 |-- penalty: integer (nullable = true)
 |-- bowler_extras: integer (nullable = true)
 |-- out_type: string (nullable = true)
 |-- caught: boolean (nullable = true)
 |-- bowled: boolean (nullable = true)
 |-- run_out: boolean (nullable = true)
 |-- lbw: boolean (nullable = true)
 |-- retired_hurt: boolean (nullable = true)
 |-- stumped: boolean (nullable = true)
 |-- caught_and_bowled: boolean (null

In [0]:
player_match_joined_player.printSchema()

root
 |-- player_match_sk: integer (nullable = true)
 |-- playermatch_key: decimal(10,0) (nullable = true)
 |-- match_id: integer (nullable = true)
 |-- player_id: integer (nullable = true)
 |-- player_name: string (nullable = true)
 |-- dob: date (nullable = true)
 |-- batting_hand: string (nullable = true)
 |-- bowling_skill: string (nullable = true)
 |-- country_name: string (nullable = true)
 |-- role_desc: string (nullable = true)
 |-- player_team: string (nullable = true)
 |-- opposit_team: string (nullable = true)
 |-- season_year: integer (nullable = true)
 |-- is_manofthematch: boolean (nullable = true)
 |-- age_as_on_match: integer (nullable = true)
 |-- isplayers_team_won: boolean (nullable = true)
 |-- batting_status: string (nullable = true)
 |-- bowling_status: string (nullable = true)
 |-- player_captain: string (nullable = true)
 |-- opposit_captain: string (nullable = true)
 |-- player_keeper: string (nullable = true)
 |-- opposit_keeper: string (nullable = true)
 |-- 

In [0]:
ball_by_ball_joined_match__joined__player_match_joined_player = ball_by_ball_joined_match.join(player_match_joined_player, "match_id", "outer")
ball_by_ball_joined_match__joined__player_match_joined_player.show(100)

+--------+-------+-------+----------+------------+------------+------------------------+----------+-----------+----------+-----+-------+----+-------+-------+-------------+--------------+------+------+-------+----+------------+-------+-----------------+----------+----------------+-------------+----------+------+-------+-----------+------+----------+--------+----------------+---------+-------------------+-------------+----------------+----------+---------------+---------+------------------+--------------+--------------+------------+-------------+-----------+--------+----------------+---------------+----------+-----------+--------------------+---------+------------+---------------+----------------+---------+--------+------------+---------+----------+----------+---------------+---------------+---------+----------------+----+--------------+--------------------+------------+---------+----------------+----------------+-----------+----------------+---------------+------------------+-----------

In [0]:
ball_by_ball_joined_match__joined__player_match_joined_player.printSchema()

root
 |-- match_id: integer (nullable = true)
 |-- over_id: integer (nullable = true)
 |-- ball_id: integer (nullable = true)
 |-- innings_no: integer (nullable = true)
 |-- team_batting: string (nullable = true)
 |-- team_bowling: string (nullable = true)
 |-- striker_batting_position: integer (nullable = true)
 |-- extra_type: string (nullable = true)
 |-- runs_scored: integer (nullable = true)
 |-- extra_runs: integer (nullable = true)
 |-- wides: integer (nullable = true)
 |-- legbyes: integer (nullable = true)
 |-- byes: integer (nullable = true)
 |-- noballs: integer (nullable = true)
 |-- penalty: integer (nullable = true)
 |-- bowler_extras: integer (nullable = true)
 |-- out_type: string (nullable = true)
 |-- caught: boolean (nullable = true)
 |-- bowled: boolean (nullable = true)
 |-- run_out: boolean (nullable = true)
 |-- lbw: boolean (nullable = true)
 |-- retired_hurt: boolean (nullable = true)
 |-- stumped: boolean (nullable = true)
 |-- caught_and_bowled: boolean (null

In [0]:
# Print just the list of column names
print(ball_by_ball_joined_match__joined__player_match_joined_player.columns)

['match_id', 'over_id', 'ball_id', 'innings_no', 'team_batting', 'team_bowling', 'striker_batting_position', 'extra_type', 'runs_scored', 'extra_runs', 'wides', 'legbyes', 'byes', 'noballs', 'penalty', 'bowler_extras', 'out_type', 'caught', 'bowled', 'run_out', 'lbw', 'retired_hurt', 'stumped', 'caught_and_bowled', 'hit_wicket', 'obstructingfeild', 'bowler_wicket', 'match_date', 'season', 'striker', 'non_striker', 'bowler', 'player_out', 'fielders', 'striker_match_sk', 'strikersk', 'nonstriker_match_sk', 'nonstriker_sk', 'fielder_match_sk', 'fielder_sk', 'bowler_match_sk', 'bowler_sk', 'playerout_match_sk', 'battingteam_sk', 'bowlingteam_sk', 'keeper_catch', 'player_out_sk', 'matchdatesk', 'match_sk', 'team1', 'team2', 'match_date', 'season_year', 'venue_name', 'city_name', 'country_name', 'toss_winner', 'match_winner', 'toss_name', 'win_type', 'outcome_type', 'manofmach', 'win_margin', 'country_id', 'player_match_sk', 'playermatch_key', 'player_id', 'player_name', 'dob', 'batting_hand

In [0]:
ball_by_ball_joined_match__joined__player_match_joined_player.select("match_id", "season", "match_date", "team_batting", "team_bowling",
    "venue_name", "city_name", "match_winner", "win_margin", "win_type",
    "over_id", "ball_id", "innings_no", "runs_scored", "extra_runs", "bowler_extras",
    "out_type", "striker", "non_striker", "bowler", "player_out", "fielders",
    "caught", "bowled", "run_out", "lbw", "stumped", "caught_and_bowled",
    "player_name", "batting_hand", "bowling_skill", "role_desc").show(5)

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-3118391048556061>:1
----> 1 ball_by_ball_joined_match__joined__player_match_joined_player.select("match_id", "season", "match_date", "team_batting", "team_bowling",
      2     "venue_name", "city_name", "match_winner", "win_margin", "win_type",
      3     "over_id", "ball_id", "innings_no", "runs_scored", "extra_runs", "bowler_extras",
      4     "out_type", "striker", "non_striker", "bowler", "player_out", "fielders",
      5     "caught", "bowled", "run_out", "lbw", "stumped", "caught_and_bowled",
      6     "player_name", "batting_hand", "bowling_skill", "role_desc").show(5)

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
    

In [0]:
final_df = ball_by_ball_joined_match__joined__player_match_joined_player.select("match_id", "season", "team_batting", "team_bowling", "venue_name", "city_name",
                                                                     "match_winner", "win_margin", "win_type",
                                                                     "over_id", "ball_id", "innings_no", "runs_scored", "extra_runs", "bowler_extras",
                                                                     "out_type", "striker", "non_striker", "bowler", "player_out", "fielders",
                                                                     "caught", "bowled", "run_out", "lbw", "stumped", "caught_and_bowled",
                                                                     "role_desc")

In [0]:
# Convert Spark DataFrame to Pandas DataFrame
pandas_df = final_df.toPandas()

In [0]:
final_df.show(5)

+--------+------+------------+------------+--------------------+---------+----------------+----------+--------+-------+-------+----------+-----------+----------+-------------+--------------+-------+-----------+------+----------+--------+------+------+-------+----+-------+-----------------+---------+
|match_id|season|team_batting|team_bowling|          venue_name|city_name|    match_winner|win_margin|win_type|over_id|ball_id|innings_no|runs_scored|extra_runs|bowler_extras|      out_type|striker|non_striker|bowler|player_out|fielders|caught|bowled|run_out| lbw|stumped|caught_and_bowled|role_desc|
+--------+------+------------+------------+--------------------+---------+----------------+----------+--------+-------+-------+----------+-----------+----------+-------------+--------------+-------+-----------+------+----------+--------+------+------+-------+----+-------+-----------------+---------+
|      -1|  null|        null|        null|                null|     null|            null|      

In [0]:
# Displaying it in tabular format
display(final_df)

match_id season team_batting team_bowling venue_name city_name match_winner win_margin win_type over_id ball_id innings_no runs_scored extra_runs bowler_extras out_type striker non_striker bowler player_out fielders caught bowled run_out lbw stumped caught_and_bowled role_desc -1 null null null null null null null null null null null null null null null null null null null null null null null null null null null 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Keeper 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Captain 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Captain 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Keeper 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 1 1 0 0 0 Not Applicable 24 25 126 null null null null null null null null Player 335992 2008 4 5 Sawai Mansingh Stadium Jaipur Rajasthan Royals 6 wickets 1 2 1 0 0 0 Not Applicable 24 25 126 null null null nul

### Note: Un-finished work
#### Need to rework on the final_df 
###### Business and sports analytical questions are answered correctly.